In [1]:
#import all necessary libraries and packages

import numpy as np 
import pandas as pd
from collections import defaultdict
import requests
import csv

from scipy.stats import norm

from bokeh.plotting import show, figure
from bokeh.models import ColumnDataSource, HoverTool
from bokeh.palettes import Viridis6


import math
import datetime

import matplotlib.pyplot as plt
import seaborn as sns
color = sns.color_palette()
%matplotlib inline

import plotly.offline as py
from plotly import tools
py.init_notebook_mode(connected=True)
import plotly.graph_objs as go
import plotly.express as px

pd.options.mode.chained_assignment = None
pd.set_option('display.max_rows', 500)
pd.set_option('display.max_columns', 500)
pd.set_option('display.width', 150)

In [2]:
#read data from the Covid Tracking project. More info can be found at www.covidtracking.com

#read state-by-state data that has information on positives, negatives, deaths, and daily increase values for each of these parameters
states_historical_df = pd.read_csv('https://covidtracking.com/api/v1/states/daily.csv')

#read state-by-state population data from the United States Census
states_pop = pd.read_csv('http://www2.census.gov/programs-surveys/popest/datasets/2010-2019/national/totals/nst-est2019-alldata.csv?#')
states_pop = states_pop[["NAME","POPESTIMATE2019"]][5:] #extract from states_pop just the state and corresponding population estimate for 2019.  


states_historical_df["date"] = pd.to_datetime(states_historical_df["date"], format="%Y%m%d").dt.date.astype(str)

#extract all unique date values in the date column
date_values = states_historical_df["date"].unique()

#This dictionary will be used for column remapping of state names later on as needed
state_map_dict = {'AL': 'Alabama',
 'AK': 'Alaska',
 'AS': 'American Samoa',
 'AZ': 'Arizona',
 'AR': 'Arkansas',
 'CA': 'California',
 'CO': 'Colorado',
 'CT': 'Connecticut',
 'DE': 'Delaware',
 'DC': 'District of Columbia',
 'FM': 'Federated States of Micronesia',
 'FL': 'Florida',
 'GA': 'Georgia',
 'GU': 'Guam',
 'HI': 'Hawaii',
 'ID': 'Idaho',
 'IL': 'Illinois',
 'IN': 'Indiana',
 'IA': 'Iowa',
 'KS': 'Kansas',
 'KY': 'Kentucky',
 'LA': 'Louisiana',
 'ME': 'Maine',
 'MH': 'Marshall Islands',
 'MD': 'Maryland',
 'MA': 'Massachusetts',
 'MI': 'Michigan',
 'MN': 'Minnesota',
 'MS': 'Mississippi',
 'MO': 'Missouri',
 'MT': 'Montana',
 'NE': 'Nebraska',
 'NV': 'Nevada',
 'NH': 'New Hampshire',
 'NJ': 'New Jersey',
 'NM': 'New Mexico',
 'NY': 'New York',
 'NC': 'North Carolina',
 'ND': 'North Dakota',
 'MP': 'Northern Mariana Islands',
 'OH': 'Ohio',
 'OK': 'Oklahoma',
 'OR': 'Oregon',
 'PW': 'Palau',
 'PA': 'Pennsylvania',
 'PR': 'Puerto Rico',
 'RI': 'Rhode Island',
 'SC': 'South Carolina',
 'SD': 'South Dakota',
 'TN': 'Tennessee',
 'TX': 'Texas',
 'UT': 'Utah',
 'VT': 'Vermont',
 'VI': 'Virgin Islands',
 'VA': 'Virginia',
 'WA': 'Washington',
 'WV': 'West Virginia',
 'WI': 'Wisconsin',
 'WY': 'Wyoming'}

#since some of our data uses full state names as opposed to the two letter denotion, we will also the invert state_map_dict dictionary
state_map_dict_inverted = {y:x for x,y in state_map_dict.items()}

state_list=list(state_map_dict.keys())

#use the state_map_dict_inverted dictionary to replace all state names with their 2 letter denotion
states_pop = states_pop.replace({"NAME": state_map_dict_inverted})

#merge the Covid Tracking project dataframe with the US Census Population dataframe
states_historical_df_pop = pd.merge(states_historical_df, states_pop, how='inner', left_on = 'state', right_on = 'NAME').drop(columns="NAME")

#Calculate Mortality Rate as the number of deaths normalized by population
states_historical_df_pop['Mortality Rate (%)']  = states_historical_df_pop["death"]*100/states_historical_df_pop["totalTestResults"]

states_historical_df_pop = states_historical_df_pop.round({'Mortality Rate (%)':2})

states_historical_df_pop


date state  positive  negative  pending  hospitalizedCurrently  hospitalizedCumulative  inIcuCurrently  inIcuCumulative  \
0     2020-04-13    AK     277.0    7553.0      NaN                    NaN                    32.0             NaN              NaN   
1     2020-04-12    AK     272.0    7766.0      NaN                    NaN                    31.0             NaN              NaN   
2     2020-04-11    AK     257.0    7475.0      NaN                    NaN                    31.0             NaN              NaN   
3     2020-04-10    AK     246.0    7186.0      NaN                    NaN                    28.0             NaN              NaN   
4     2020-04-09    AK     235.0    6988.0      NaN                    NaN                    27.0             NaN              NaN   
...          ...   ...       ...       ...      ...                    ...                     ...             ...              ...   
2047  2020-03-11    WY       0.0       NaN      NaN                    NaN                     NaN             NaN              NaN   
2048  2020-03-10    WY       0.0       0.0      0.0                    NaN                     NaN             NaN              NaN   
2049  2020-03-09    WY       0.0       NaN      NaN                    NaN                     NaN             NaN              NaN   
2050  2020-03-08    WY       0.0       NaN      NaN                    NaN                     NaN             NaN              NaN   
2051  2020-03-07    WY       0.0       NaN      NaN                    NaN                     NaN             NaN              NaN   

      onVentilatorCurrently  onVentilatorCumulative  recovered                                      hash           dateChecked  death  hospitalized  \
0                       NaN                     NaN       85.0  67560e7c63366eea20aa9e68ec2f1d41b712ce9a  2020-04-13T20:00:00Z    8.0          32.0   
1                       NaN                     NaN       66.0  5f686eece203e247c3bfb219c664517920d7c141  2020-04-12T20:00:00Z    8.0          31.0   
2                       NaN                     NaN       63.0  a8d36e9ce19edaeaac989881abf96fc74196efba  2020-04-11T20:00:00Z    8.0          31.0   
3                       NaN                     NaN       55.0  f72f6232f47812a602059afa4d5f4d698726aa3b  2020-04-10T20:00:00Z    7.0          28.0   
4                       NaN                     NaN       49.0  b25c4a1e5bb964d05142022307f57e41e0872f26  2020-04-09T20:00:00Z    7.0          27.0   
...                     ...                     ...        ...                                       ...                   ...    ...           ...   
2047                    NaN                     NaN        NaN  b2a970a45b39b2c7ec078c35757610c22241c0f6  2020-03-11T20:00:00Z    NaN           NaN   
2048                    NaN                     NaN        NaN  7386ca913797703a8f0738ff599605f36db6d06b  2020-03-10T20:00:00Z    NaN           NaN   
2049                    NaN                     NaN        NaN  c052da9af9257ed5150197a38c4d1cf9cb5992b0  2020-03-09T20:00:00Z    NaN           NaN   
2050                    NaN                     NaN        NaN  04b812c8dbb7bd7a7c1c24bb7e3b1116fb1cfa96  2020-03-08T20:00:00Z    NaN           NaN   
2051                    NaN                     NaN        NaN  265de6c0d476b4e78ad567a501a52ea9d1846184  2020-03-07T21:00:00Z    NaN           NaN   

       total  totalTestResults  posNeg  fips  deathIncrease  hospitalizedIncrease  negativeIncrease  positiveIncrease  totalTestResultsIncrease  \
0     7830.0            7830.0  7830.0     2            0.0                   1.0            -213.0               5.0                    -208.0   
1     8038.0            8038.0  8038.0     2            0.0                   0.0             291.0              15.0                     306.0   
2     7732.0            7732.0  7732.0     2            1.0                   3.0             289.0              11.0                    

In [3]:
#create list of plot dates from our earliest date to our latest date of the Covid Tracking project dataset 
plot_dates = pd.date_range(date_values.min(), date_values.max())

#this function allows us to filter the large multi-state Covid Tracking project dataset by a specific state
def statefilter(state_input):
    print(type(state_input))
    return states_historical_df_pop[states_historical_df_pop["state"]== state_input]


#create a dictionary of dataframes, df_by_state, that houses each state's covid and population data.  
#Then, to ensure that all states start data on the same date (some states started reporting later than others), 
#we expand each state's dataframe out to the earliest date in plot_dates and fill those un-entered dates with 0s

df_by_state = {}

for state in state_list:
    df_by_state[state] = statefilter(state)
    temp_state_df = df_by_state[state]
    datetime_index = pd.DatetimeIndex(temp_state_df['date'].values)
    temp_state_df.set_index(datetime_index, inplace=True)
    temp_state_df = temp_state_df.drop('date', 1)
    temp_state_df = temp_state_df.reindex(plot_dates, fill_value=None)
    temp_state_df["state"] = temp_state_df["state"].fillna(state)
    temp_state_df["positive"] = temp_state_df["positive"].fillna(0)
    temp_state_df["totalTestResults"] = temp_state_df["totalTestResults"].fillna(0)

    df_by_state[state] = temp_state_df

column_names = df_by_state["IL"].columns

df_by_state_cleaned = pd.DataFrame(columns = column_names)

#we reassign the cleaned state-by-state dataframes to 'df_by_state_cleaned' and reset the index column
for state in state_list:
    df_by_state_cleaned = df_by_state_cleaned.append(df_by_state[state])
    
df_by_state_cleaned = df_by_state_cleaned.rename_axis('date').reset_index()
df_by_state_cleaned

<class 'str'>
<class 'str'>
<class 'str'>
<class 'str'>
<class 'str'>
<class 'str'>
<class 'str'>
<class 'str'>
<class 'str'>
<class 'str'>
<class 'str'>
<class 'str'>
<class 'str'>
<class 'str'>
<class 'str'>
<class 'str'>
<class 'str'>
<class 'str'>
<class 'str'>
<class 'str'>
<class 'str'>
<class 'str'>
<class 'str'>
<class 'str'>
<class 'str'>
<class 'str'>
<class 'str'>
<class 'str'>
<class 'str'>
<class 'str'>
<class 'str'>
<class 'str'>
<class 'str'>
<class 'str'>
<class 'str'>
<class 'str'>
<class 'str'>
<class 'str'>
<class 'str'>
<class 'str'>
<class 'str'>
<class 'str'>
<class 'str'>
<class 'str'>
<class 'str'>
<class 'str'>
<class 'str'>
<class 'str'>
<class 'str'>
<class 'str'>
<class 'str'>
<class 'str'>
<class 'str'>
<class 'str'>
<class 'str'>
<class 'str'>
<class 'str'>
<class 'str'>
<class 'str'>


date state  positive  negative  pending  hospitalizedCurrently  hospitalizedCumulative  inIcuCurrently  inIcuCumulative  \
0    2020-02-28    AL       0.0       NaN      NaN                    NaN                     NaN             NaN              NaN   
1    2020-02-29    AL       0.0       NaN      NaN                    NaN                     NaN             NaN              NaN   
2    2020-03-01    AL       0.0       NaN      NaN                    NaN                     NaN             NaN              NaN   
3    2020-03-02    AL       0.0       NaN      NaN                    NaN                     NaN             NaN              NaN   
4    2020-03-03    AL       0.0       NaN      NaN                    NaN                     NaN             NaN              NaN   
...         ...   ...       ...       ...      ...                    ...                     ...             ...              ...   
2709 2020-04-09    WY     230.0    3920.0      NaN                    NaN                    34.0             NaN              NaN   
2710 2020-04-10    WY     320.0    4736.0      NaN                    NaN                    37.0             NaN              NaN   
2711 2020-04-11    WY     261.0    5198.0      NaN                    NaN                    37.0             NaN              NaN   
2712 2020-04-12    WY     261.0    5198.0      NaN                    NaN                    40.0             NaN              NaN   
2713 2020-04-13    WY     275.0    5689.0      NaN                    NaN                    41.0             NaN              NaN   

      onVentilatorCurrently  onVentilatorCumulative  recovered                                      hash           dateChecked  death  hospitalized  \
0                       NaN                     NaN        NaN                                       NaN                   NaN    NaN           NaN   
1                       NaN                     NaN        NaN                                       NaN                   NaN    NaN           NaN   
2                       NaN                     NaN        NaN                                       NaN                   NaN    NaN           NaN   
3                       NaN                     NaN        NaN                                       NaN                   NaN    NaN           NaN   
4                       NaN                     NaN        NaN                                       NaN                   NaN    NaN           NaN   
...                     ...                     ...        ...                                       ...                   ...    ...           ...   
2709                    NaN                     NaN       94.0  231a30211b44fe5c73eef7f2161a0d501c682df9  2020-04-09T20:00:00Z    0.0          34.0   
2710                    NaN                     NaN      105.0  56031032dfee2e1640993e66764150655694c0a6  2020-04-10T20:00:00Z    0.0          37.0   
2711                    NaN                     NaN      129.0  ec8a322ffba1a10858e7b2e45c9d6febda25d776  2020-04-11T20:00:00Z    0.0          37.0   
2712                    NaN                     NaN      137.0  2a6cd1a98f43d43820dfb2d7cb95355af66c516b  2020-04-12T20:00:00Z    0.0          40.0   
2713                    NaN                     NaN      138.0  925408d55d0948b12058c56e5c0acd2eb3b0f93d  2020-04-13T20:00:00Z    1.0          41.0   

       total  totalTestResults  posNeg  fips  deathIncrease  hospitalizedIncrease  negativeIncrease  positiveIncrease  totalTestResultsIncrease  \
0        NaN               0.0     NaN   NaN            NaN                   NaN               NaN               NaN                       NaN   
1        NaN               0.0     NaN   NaN            NaN                   NaN               NaN               NaN                       NaN   
2        NaN               0.0     NaN   NaN            NaN                   NaN               NaN               NaN                       NaN   
3

In [4]:
cumulative_df = states_historical_df_pop.groupby(["state","date"])["state","positive", "death", "negative", "total", "fips","POPESTIMATE2019"].sum().reset_index()

#cumulative_df["date"] = pd.to_datetime(cumulative_df["date"] , format="%Y-%m-%d").dt.date
#cumulative_df = cumulative_df.sort_values(by="date").reset_index(drop=True)
#start_date = datetime.date(2020, 3, 7)
#cumulative_df = cumulative_df[cumulative_df["date"]>=start_date]
#cumulative_df["date"] = cumulative_df["date"].astype(str)

#fig = px.choropleth(locations=cumulative_df["state"],
                    #color=cumulative_df["positive"]/cumulative_df["POPESTIMATE2019"]*100000, 
                    #locationmode="USA-states",
                    #scope="usa",
                    #animation_frame=cumulative_df["date"],
                    #color_continuous_scale='Reds',
                    #range_color=[0,100]
                    #autocolorscale=False,
                   #)


##layout = go.Layout(
#    title=go.layout.Title(
#        text="Cumulative count of positive COVID-19 cases in US states per 100,000 people",
#        x=0.5
#    ),
#    font=dict(size=14),
#)

#fig.update_layout(layout)
#fig.show()
cumulative_df[cumulative_df["state"]=="IL"]


C:\Users\aelkhatib\Anaconda3\lib\site-packages\ipykernel_launcher.py:1: FutureWarning:

Indexing with multiple keys (implicitly converted to a tuple of keys) will be deprecated, use a list instead.



state        date  positive  death  negative     total  fips  POPESTIMATE2019
552    IL  2020-03-04       4.0    0.0     124.0     155.0    17         12671821
553    IL  2020-03-05       5.0    0.0     165.0     197.0    17         12671821
554    IL  2020-03-06       5.0    0.0     180.0     220.0    17         12671821
555    IL  2020-03-07       6.0    0.0     191.0     241.0    17         12671821
556    IL  2020-03-08       6.0    0.0     191.0     241.0    17         12671821
557    IL  2020-03-09       7.0    0.0     191.0     242.0    17         12671821
558    IL  2020-03-10      19.0    0.0     244.0     326.0    17         12671821
559    IL  2020-03-11      19.0    0.0     244.0     326.0    17         12671821
560    IL  2020-03-12      25.0    0.0     266.0     367.0    17         12671821
561    IL  2020-03-13      32.0    0.0     294.0     418.0    17         12671821
562    IL  2020-03-14      46.0    0.0     316.0     444.0    17         12671821
563    IL  2020-03-15      64.0    0.0     449.0     708.0    17         12671821
564    IL  2020-03-16      93.0    0.0     932.0    1025.0    17         12671821
565    IL  2020-03-17     159.0    1.0    1340.0    1499.0    17         12671821
566    IL  2020-03-18     288.0    1.0    1763.0    2051.0    17         12671821
567    IL  2020-03-19     422.0    4.0    2725.0    3147.0    17         12671821
568    IL  2020-03-20     585.0    5.0    3696.0    4281.0    17         12671821
569    IL  2020-03-21     753.0    6.0    5488.0    6241.0    17         12671821
570    IL  2020-03-22    1049.0    9.0    7271.0    8320.0    17         12671821
571    IL  2020-03-23    1273.0   12.0    8583.0    9856.0    17         12671821
572    IL  2020-03-24    1535.0   16.0    9934.0   11469.0    17         12671821
573    IL  2020-03-25    1865.0   19.0   12344.0   14209.0    17         12671821
574    IL  2020-03-26    2538.0   26.0   14093.0   16631.0    17         12671821
575    IL  2020-03-27    3026.0   34.0   18516.0   21542.0    17         12671821
576    IL  2020-03-28    3491.0   47.0   22000.0   25491.0    17         12671821
577    IL  2020-03-29    4596.0   65.0   23166.0   27762.0    17         12671821
578    IL  2020-03-30    5057.0   73.0   25389.0   30446.0    17         12671821
579    IL  2020-03-31    5994.0   99.0   29231.0   35225.0    17         12671821
580    IL  2020-04-01    6980.0  141.0   33404.0   40384.0    17         12671821
581    IL  2020-04-02    7695.0  157.0   35961.0   43656.0    17         12671821
582    IL  2020-04-03    8904.0  210.0   39144.0   48048.0    17         12671821
583    IL  2020-04-04   10357.0  243.0   43224.0   53581.0    17         12671821
584    IL  2020-04-05   11256.0  274.0   47727.0   58983.0    17         12671821
585    IL  2020-04-06   12262.0  307.0   50680.0   62942.0    17         12671821
586    IL  2020-04-07   13549.0  380.0   55183.0   68732.0    17         12671821
587    IL  2020-04-08   15078.0  462.0   59988.0   75066.0    17         12671821
588    IL  2020-04-09   16422.0  528.0   64435.0   80857.0    17         12671821
589    IL  2020-04-10   17887.0  596.0   69640.0   87527.0    17         12671821
590    IL  2020-04-11   19180.0  677.0   72969.0   92149.0    17         12671821
591    IL  2020-04-12   20852.0  720.0   79883.0  100735.0    17         12671821
592    IL  2020-04-13   22025.0  794.0   83743.0  105768.0    17         12671821

In [5]:
fig = px.choropleth(locations=cumulative_df["state"],
                    color=cumulative_df["negative"], 
                    locationmode="USA-states",
                    scope="usa",
                    animation_frame=cumulative_df["date"],
                    color_continuous_scale='Greens',
                    range_color=[0,5000]
                    #autocolorscale=False,
                   )

layout = go.Layout(
    title=go.layout.Title(
        text="Cumulative count of COVID-19 cases in US states",
        x=0.5
    ),
    font=dict(size=14),
)

fig.update_layout(layout)
fig.show()

df_by_state["AL"]["positive"]

2020-02-28       0.0
2020-02-29       0.0
2020-03-01       0.0
2020-03-02       0.0
2020-03-03       0.0
2020-03-04       0.0
2020-03-05       0.0
2020-03-06       0.0
2020-03-07       0.0
2020-03-08       0.0
2020-03-09       0.0
2020-03-10       0.0
2020-03-11       0.0
2020-03-12       0.0
2020-03-13       1.0
2020-03-14       6.0
2020-03-15      12.0
2020-03-16      28.0
2020-03-17      36.0
2020-03-18      46.0
2020-03-19      68.0
2020-03-20      81.0
2020-03-21     124.0
2020-03-22     138.0
2020-03-23     167.0
2020-03-24     215.0
2020-03-25     283.0
2020-03-26     506.0
2020-03-27     587.0
2020-03-28     696.0
2020-03-29     806.0
2020-03-30     859.0
2020-03-31     981.0
2020-04-01    1077.0
2020-04-02    1233.0
2020-04-03    1432.0
2020-04-04    1580.0
2020-04-05    1796.0
2020-04-06    1968.0
2020-04-07    2119.0
2020-04-08    2369.0
2020-04-09    2769.0
2020-04-10    2968.0
2020-04-11    3191.0
2020-04-12    3525.0
2020-04-13    3734.0
Freq: D, Name: positive, dtype: fl

In [6]:
import plotly.express as px


fig = px.scatter(states_historical_df_pop, x="total", y="positive", animation_frame="date", animation_group="state",
           size="positive", color="state", hover_name="state",
           log_x=False, size_max=55, range_x=[0,250000], range_y=[0,100000])

layout = go.Layout(
    title=go.layout.Title(
        text="Total testing counts Vs Positive Counts over time",
        x=0.5
    ),
    font=dict(size=14),
#     width=800,
#     height=500,
    xaxis_title = "Total number of tests",
    yaxis_title = "Number of positive tests"
)

fig.update_layout(layout)
fig.show()
fig.write_html('positives_to_total_figure.html', auto_open=True)


In [7]:
df_by_state_cleaned["date"] = pd.to_datetime(df_by_state_cleaned["date"] , format="%m/%d/%Y").dt.date

df_by_state_cleaned = df_by_state_cleaned.sort_values(by="date").reset_index(drop = True)

df_by_state_cleaned["date"] = df_by_state_cleaned["date"].astype(str)

fig = px.scatter(df_by_state_cleaned, x="positive", y="death", animation_frame="date", animation_group="state",
           size="positive", color="state", hover_name="state",
           log_x=False, size_max=55, range_x=[0,120000], range_y=[0,3500])

layout = go.Layout(
    title=go.layout.Title(
        text="Positive test counts Vs deaths over time",
        x=0.5
    ),
    font=dict(size=14),
#     width=800,
#     height=500,
    xaxis_title = "Total number of positive tests",
    yaxis_title = "Number of deaths"
)

fig.update_layout(layout)
fig.update_layout(showlegend=False)

fig.show()
fig.write_html('deaths_to_positive_figure.html', auto_open=False)


In [8]:
states_historical_df_pop_NY = df_by_state_cleaned[df_by_state_cleaned["state"] == "IL"]

fig = px.line(states_historical_df_pop_NY, x="date", y="Mortality Rate (%)")

#fig.update_layout(yaxis_type="log")

layout = go.Layout(
    title=go.layout.Title(
        text="Illinois Positive Cases Over Time",
        x=0.5
    ),
    font=dict(size=14),
#     width=800,
#     height=500,
    xaxis_title = "Date",
    yaxis_title = "log(Positive Cases)"
)
fig.update_layout(layout)
fig.show()
#fig.write_html('positive_tests_over_time_figure.html', auto_open=False)
states_historical_df_pop_NY

date state  positive  negative  pending  hospitalizedCurrently  hospitalizedCumulative  inIcuCurrently  inIcuCumulative  \
28    2020-02-28    IL       0.0       NaN      NaN                    NaN                     NaN             NaN              NaN   
95    2020-02-29    IL       0.0       NaN      NaN                    NaN                     NaN             NaN              NaN   
155   2020-03-01    IL       0.0       NaN      NaN                    NaN                     NaN             NaN              NaN   
204   2020-03-02    IL       0.0       NaN      NaN                    NaN                     NaN             NaN              NaN   
255   2020-03-03    IL       0.0       NaN      NaN                    NaN                     NaN             NaN              NaN   
329   2020-03-04    IL       4.0     124.0     27.0                    NaN                     NaN             NaN              NaN   
368   2020-03-05    IL       5.0     165.0     27.0                    NaN                     NaN             NaN              NaN   
414   2020-03-06    IL       5.0     180.0     35.0                    NaN                     NaN             NaN              NaN   
513   2020-03-07    IL       6.0     191.0     44.0                    NaN                     NaN             NaN              NaN   
546   2020-03-08    IL       6.0     191.0     44.0                    NaN                     NaN             NaN              NaN   
611   2020-03-09    IL       7.0     191.0     44.0                    NaN                     NaN             NaN              NaN   
676   2020-03-10    IL      19.0     244.0     63.0                    NaN                     NaN             NaN              NaN   
730   2020-03-11    IL      19.0     244.0     63.0                    NaN                     NaN             NaN              NaN   
814   2020-03-12    IL      25.0     266.0     76.0                    NaN                     NaN             NaN              NaN   
850   2020-03-13    IL      32.0     294.0     92.0                    NaN                     NaN             NaN              NaN   
930   2020-03-14    IL      46.0     316.0     82.0                    NaN                     NaN             NaN              NaN   
981   2020-03-15    IL      64.0     449.0    195.0                    NaN                     NaN             NaN              NaN   
1034  2020-03-16    IL      93.0     932.0      NaN                    NaN                     NaN             NaN              NaN   
1115  2020-03-17    IL     159.0    1340.0      NaN                    NaN                     NaN             NaN              NaN   
1139  2020-03-18    IL     288.0    1763.0      NaN                    NaN                     NaN             NaN              NaN   
1214  2020-03-19    IL     422.0    2725.0      NaN                    NaN                     NaN             NaN              NaN   
1294  2020-03-20    IL     585.0    3696.0      NaN                    NaN                     NaN             NaN              NaN   
1331  2020-03-21    IL     753.0    5488.0      NaN                    NaN                     NaN             NaN              NaN   
1388  2020-03-22    IL    1049.0    7271.0      NaN                    NaN                     NaN             NaN              NaN   
1451  2020-03-23    IL    1273.0    8583.0      NaN                    NaN                     NaN             NaN              NaN   
1486  2020-03-24    IL    1535.0    9934.0      NaN                    NaN                     NaN             NaN              NaN   
1550  2020-03-25    IL    1865.0   12344.0      NaN                    NaN                     NaN             NaN              NaN   
1593  2020-03-26    IL    2538.0   14093.0      NaN                    NaN                     NaN             NaN              NaN   
1653  2020-03-27    IL    3026.0   18516.0      NaN                    NaN                     Na

In [43]:
county_historical_sum = pd.read_csv('https://github.com/nytimes/covid-19-data/raw/master/us-counties.csv')

county_historical_sum = county_historical_sum.groupby(["state","county","fips"])["cases","deaths"].sum().reset_index()

#This needs to be grouped again !!!!!!!!
county_demographics_2019_df_sum = pd.read_csv('https://www2.census.gov/programs-surveys/popest/datasets/2010-2018/counties/asrh/cc-est2018-alldata.csv', encoding='ISO-8859-1')


county_demographics_2019_df_sum["HA_MALE"]=county_demographics_2019_df_sum["WA_MALE"]-county_demographics_2019_df_sum["NHWAC_MALE"]
county_demographics_2019_df_sum["HA_FEMALE"]=county_demographics_2019_df_sum["WA_FEMALE"]-county_demographics_2019_df_sum["NHWAC_FEMALE"]


#county_historical_sum['fips'] = county_historical_sum['fips'].astype(int)
county_demographics_2019_df_sum['COUNTY'] = county_demographics_2019_df_sum['COUNTY'].astype(int)

county_demographics_2019_df_sum['COUNTY'] = (county_demographics_2019_df_sum['STATE']*1000) + county_demographics_2019_df_sum['COUNTY']

county_demographics_2019_df_sum = county_demographics_2019_df_sum[county_demographics_2019_df_sum["YEAR"]==11].groupby(["STATE","COUNTY"])["TOT_POP","TOT_MALE","TOT_FEMALE","WA_MALE","WA_FEMALE","BA_MALE","BA_FEMALE","AA_MALE","AA_FEMALE","IA_MALE","IA_FEMALE","NA_MALE","NA_FEMALE","HA_MALE","HA_FEMALE"].sum().reset_index()



county_race_covid_2019_df = pd.merge(county_demographics_2019_df_sum, county_historical_sum, left_on = 'COUNTY', right_on = 'fips', how = "inner")


county_race_covid_2019_df

C:\Users\aelkhatib\Anaconda3\lib\site-packages\ipykernel_launcher.py:3: FutureWarning:

Indexing with multiple keys (implicitly converted to a tuple of keys) will be deprecated, use a list instead.

C:\Users\aelkhatib\Anaconda3\lib\site-packages\ipykernel_launcher.py:18: FutureWarning:

Indexing with multiple keys (implicitly converted to a tuple of keys) will be deprecated, use a list instead.



STATE  COUNTY  TOT_POP  TOT_MALE  TOT_FEMALE  WA_MALE  WA_FEMALE  BA_MALE  BA_FEMALE  AA_MALE  AA_FEMALE  IA_MALE  IA_FEMALE  NA_MALE  \
0         1    1001   111202     53990       57212    41718      43602    10306      11524      602        760      242        292       66   
1         1    1003   436044    211314      224730   184942     195660    18800      20184     1866       3150     1772       1596      146   
2         1    1005    49762     26266       23496    12820      11598    12740      11344      104        122      194        134       60   
3         1    1007    44800     23842       20958    17524      16898     5908       3632       38         68       96        100       44   
4         1    1009   115680     57000       58680    54614      56298     1014        886      164        206      390        366       88   
...     ...     ...      ...       ...         ...      ...        ...      ...        ...      ...        ...      ...        ...      ...   
2662     56   56035    19626     10590        9036    10116       8664      116         60       72         72      138         96        4   
2663     56   56037    86102     44304       41798    41668      39126      656        528      364        506      644        686       68   
2664     56   56039    46162     23818       22344    22714      21228      200        150      264        388      220        202       40   
2665     56   56041    40598     20570       20028    19636      19076      156        180       82        110      264        312       34   
2666     56   56043    15770      7976        7794     7556       7344       50         30       56         74      130        156       10   

      NA_FEMALE  HA_MALE  HA_FEMALE    state      county     fips  cases  deaths  
0            58      526        470  Alabama     Autauga   1001.0    207       7  
1           146     6292       5286  Alabama     Baldwin   1003.0    618      12  
2            32      694        562  Alabama     Barbour   1005.0     50       0  
3             8      366        224  Alabama        Bibb   1007.0    102       0  
4            52     4894       4136  Alabama      Blount   1009.0    147       0  
...         ...      ...        ...      ...         ...      ...    ...     ...  
2662          4      576        490  Wyoming    Sublette  56035.0     16       0  
2663         68     5896       5276  Wyoming  Sweetwater  56037.0     70       0  
2664         30     2994       2794  Wyoming       Teton  56039.0    601       0  
2665         26     1338       1322  Wyoming       Uinta  56041.0     30       0  
2666          6      858        798  Wyoming    Washakie  56043.0     44       0  

[2667 rows x 22 columns]

In [44]:

#Rename COUNTY to COUNTY FIPS and STATE to STATE FIPS, then move state and county to the front.  thanks bro
#county_race_covid_2019_df['STATE'] = county_race_covid_2019_df['STATE'].astype(str)

#county_race_covid_2019_df = county_race_covid_2019_df.replace({"STATE": state_codes_swap})

county_race_covid_2019_df = county_race_covid_2019_df.rename(columns={'COUNTY': 'COUNTY_FIPS', 'STATE': 'STATE_FIPS'})
temp = county_race_covid_2019_df['state']
county_race_covid_2019_df.drop(labels=['state'], axis=1, inplace = True)
county_race_covid_2019_df.insert(0, 'state', temp)
temp2 = county_race_covid_2019_df['county']
county_race_covid_2019_df.drop(labels=['county'], axis=1, inplace = True)
county_race_covid_2019_df.insert(1, 'county', temp2)


county_race_covid_2019_df


state      county  STATE_FIPS  COUNTY_FIPS  TOT_POP  TOT_MALE  TOT_FEMALE  WA_MALE  WA_FEMALE  BA_MALE  BA_FEMALE  AA_MALE  AA_FEMALE  \
0     Alabama     Autauga           1         1001   111202     53990       57212    41718      43602    10306      11524      602        760   
1     Alabama     Baldwin           1         1003   436044    211314      224730   184942     195660    18800      20184     1866       3150   
2     Alabama     Barbour           1         1005    49762     26266       23496    12820      11598    12740      11344      104        122   
3     Alabama        Bibb           1         1007    44800     23842       20958    17524      16898     5908       3632       38         68   
4     Alabama      Blount           1         1009   115680     57000       58680    54614      56298     1014        886      164        206   
...       ...         ...         ...          ...      ...       ...         ...      ...        ...      ...        ...      ...        ...   
2662  Wyoming    Sublette          56        56035    19626     10590        9036    10116       8664      116         60       72         72   
2663  Wyoming  Sweetwater          56        56037    86102     44304       41798    41668      39126      656        528      364        506   
2664  Wyoming       Teton          56        56039    46162     23818       22344    22714      21228      200        150      264        388   
2665  Wyoming       Uinta          56        56041    40598     20570       20028    19636      19076      156        180       82        110   
2666  Wyoming    Washakie          56        56043    15770      7976        7794     7556       7344       50         30       56         74   

      IA_MALE  IA_FEMALE  NA_MALE  NA_FEMALE  HA_MALE  HA_FEMALE     fips  cases  deaths  
0         242        292       66         58      526        470   1001.0    207       7  
1        1772       1596      146        146     6292       5286   1003.0    618      12  
2         194        134       60         32      694        562   1005.0     50       0  
3          96        100       44          8      366        224   1007.0    102       0  
4         390        366       88         52     4894       4136   1009.0    147       0  
...       ...        ...      ...        ...      ...        ...      ...    ...     ...  
2662      138         96        4          4      576        490  56035.0     16       0  
2663      644        686       68         68     5896       5276  56037.0     70       0  
2664      220        202       40         30     2994       2794  56039.0    601       0  
2665      264        312       34         26     1338       1322  56041.0     30       0  
2666      130        156       10          6      858        798  56043.0     44       0  

[2667 rows x 22 columns]

In [45]:

county_race_covid_2019_df["Total"] = county_race_covid_2019_df["TOT_MALE"]+county_race_covid_2019_df["TOT_FEMALE"]
county_race_covid_2019_df["Cases per 1000"] = county_race_covid_2019_df["cases"]/county_race_covid_2019_df["Total"]*1000
county_race_covid_2019_df["Cases per 100"] = county_race_covid_2019_df["cases"]/county_race_covid_2019_df["Total"]*100



county_race_covid_2019_df["White"] = county_race_covid_2019_df["WA_MALE"]+county_race_covid_2019_df["WA_FEMALE"]
county_race_covid_2019_df["%White"] = county_race_covid_2019_df["White"]/county_race_covid_2019_df["Total"]*100

county_race_covid_2019_df["Black"] = county_race_covid_2019_df["BA_MALE"]+county_race_covid_2019_df["BA_FEMALE"]
county_race_covid_2019_df["%Black"] = county_race_covid_2019_df["Black"]/county_race_covid_2019_df["Total"]*100

county_race_covid_2019_df["Asian"] = county_race_covid_2019_df["AA_MALE"]+county_race_covid_2019_df["AA_FEMALE"]
county_race_covid_2019_df["%Asian"] = county_race_covid_2019_df["Asian"]/county_race_covid_2019_df["Total"]*100

county_race_covid_2019_df["American Indian"] = county_race_covid_2019_df["IA_MALE"]+county_race_covid_2019_df["IA_FEMALE"]
county_race_covid_2019_df["%American Indian"] = county_race_covid_2019_df["American Indian"]/county_race_covid_2019_df["Total"]*100

county_race_covid_2019_df["Hispanic"] = county_race_covid_2019_df["HA_MALE"]+county_race_covid_2019_df["HA_FEMALE"]
county_race_covid_2019_df["%Hispanic"] = county_race_covid_2019_df["Hispanic"]/county_race_covid_2019_df["Total"]*100

county_race_covid_2019_df["Pacific Islander"] = county_race_covid_2019_df["NA_MALE"]+county_race_covid_2019_df["NA_FEMALE"]
county_race_covid_2019_df["%Pacific Islander"] = county_race_covid_2019_df["Pacific Islander"]/county_race_covid_2019_df["Total"]*100


county_race_covid_2019_df_plot = county_race_covid_2019_df[county_race_covid_2019_df["state"]=="Illinois"]


county_race_covid_2019_df

state      county  STATE_FIPS  COUNTY_FIPS  TOT_POP  TOT_MALE  TOT_FEMALE  WA_MALE  WA_FEMALE  BA_MALE  BA_FEMALE  AA_MALE  AA_FEMALE  \
0     Alabama     Autauga           1         1001   111202     53990       57212    41718      43602    10306      11524      602        760   
1     Alabama     Baldwin           1         1003   436044    211314      224730   184942     195660    18800      20184     1866       3150   
2     Alabama     Barbour           1         1005    49762     26266       23496    12820      11598    12740      11344      104        122   
3     Alabama        Bibb           1         1007    44800     23842       20958    17524      16898     5908       3632       38         68   
4     Alabama      Blount           1         1009   115680     57000       58680    54614      56298     1014        886      164        206   
...       ...         ...         ...          ...      ...       ...         ...      ...        ...      ...        ...      ...        ...   
2662  Wyoming    Sublette          56        56035    19626     10590        9036    10116       8664      116         60       72         72   
2663  Wyoming  Sweetwater          56        56037    86102     44304       41798    41668      39126      656        528      364        506   
2664  Wyoming       Teton          56        56039    46162     23818       22344    22714      21228      200        150      264        388   
2665  Wyoming       Uinta          56        56041    40598     20570       20028    19636      19076      156        180       82        110   
2666  Wyoming    Washakie          56        56043    15770      7976        7794     7556       7344       50         30       56         74   

      IA_MALE  IA_FEMALE  NA_MALE  NA_FEMALE  HA_MALE  HA_FEMALE     fips  cases  deaths   Total  Cases per 1000  Cases per 100   White     %White  \
0         242        292       66         58      526        470   1001.0    207       7  111202        1.861477       0.186148   85320  76.725239   
1        1772       1596      146        146     6292       5286   1003.0    618      12  436044        1.417288       0.141729  380602  87.285228   
2         194        134       60         32      694        562   1005.0     50       0   49762        1.004783       0.100478   24418  49.069571   
3          96        100       44          8      366        224   1007.0    102       0   44800        2.276786       0.227679   34422  76.834821   
4         390        366       88         52     4894       4136   1009.0    147       0  115680        1.270747       0.127075  110912  95.878285   
...       ...        ...      ...        ...      ...        ...      ...    ...     ...     ...             ...            ...     ...        ...   
2662      138         96        4          4      576        490  56035.0     16       0   19626        0.815245       0.081525   18780  95.689392   
2663      644        686       68         68     5896       5276  56037.0     70       0   86102        0.812989       0.081299   80794  93.835219   
2664      220        202       40         30     2994       2794  56039.0    601       0   46162       13.019367       1.301937   43942  95.190850   
2665      264        312       34         26     1338       1322  56041.0     30       0   40598        0.738953       0.073895   38712  95.354451   
2666      130        156       10          6      858        798  56043.0     44       0   15770        2.790108       0.279011   14900  94.483196   

      Black     %Black  Asian    %Asian  American Indian  %American Indian  Hispanic  %Hispanic  Pacific Islander  %Pacific Islander  
0     21830  19.630942   1362  1.224798              534          0.480207       996   0.895667               124           0.111509  
1     38984   8.940382   5016  1.150343             3368          0.772399     11578   2.655237               292           0.066966  
2     24084  48.398376    226  0.454162              328     

In [46]:
fig = px.scatter(county_race_covid_2019_df_plot, x="%Black", y="Cases per 100", hover_name= "COUNTY_FIPS",
           log_y=False, size_max=55, range_x=[0,250000], range_y=[1,100000])


#fig.add_scatter(x=county_race_covid_2019_df_plot["%White"], y=county_race_covid_2019_df_plot["cases"], mode = "markers") # Not what is desired - need a line 

fig.show()

In [47]:
cook_county_deaths = pd.read_csv("https://datacatalog.cookcountyil.gov/api/views/cjeq-bs86/rows.csv?accessType=DOWNLOAD",dtype = {"Incident Zip Code" : "str","Residence_Zip" : "str"})

cook_county_deaths = cook_county_deaths[["Case Number","Date of Death", "Age", "Gender", "Race", "Latino", "Manner of Death", "Primary Cause", "Primary Cause Line A", "Primary Cause Line B", "Primary Cause Line C", "Secondary Cause", "Incident City", "Incident Zip Code", "longitude", "latitude", "location", "Residence City", "Residence_Zip", "OBJECTID"]]

filter_statement = (cook_county_deaths["Primary Cause"].str.contains('NOVEL',na=False)) | (cook_county_deaths["Primary Cause Line A"].str.contains('NOVEL',na=False)) | (cook_county_deaths["Primary Cause Line B"].str.contains('NOVEL',na=False)) | (cook_county_deaths["Primary Cause Line C"].str.contains('NOVEL',na=False)) | (cook_county_deaths['Secondary Cause'].str.contains('NOVEL',na=False))

cook_county_deaths_cleaned = cook_county_deaths[filter_statement]


cook_county_deaths_cleaned_race = cook_county_deaths_cleaned.groupby(["Race"])["Case Number"].count().reset_index()
cook_county_deaths_cleaned_age = cook_county_deaths_cleaned.groupby(["Age"])["Case Number"].count().reset_index()

cook_county_deaths_cleaned_race["Racial Percentage"] = cook_county_deaths_cleaned_race["Case Number"]/cook_county_deaths_cleaned_race["Case Number"].sum()*100
cook_county_deaths_cleaned_age["Age Percentage"] = cook_county_deaths_cleaned_age["Case Number"]/cook_county_deaths_cleaned_race["Case Number"].sum()*100

cook_county_deaths_cleaned_age

bins= [0,5,15,20,30,40,50,60,70,105]
labels = ['0-5 yrs','5-15 yrs','15-20 yrs','20-30 yrs','30-40 yrs', "40-50 yrs", "50-60 yrs", "60-70 yrs", "70-105 yrs"]
cook_county_deaths_cleaned_age['AgeGroup'] = pd.cut(cook_county_deaths_cleaned_age['Age'], bins=bins, labels=labels, right=False)

cook_county_deaths_cleaned_age = cook_county_deaths_cleaned_age.groupby(["AgeGroup"])["Age Percentage"].sum().reset_index()
cook_county_deaths_cleaned_age

cook_county_deaths_cleaned_race


Race  Case Number  Racial Percentage
0    Asian           12           2.298851
1    Black          268          51.340996
2    Other           12           2.298851
3  Unknown            6           1.149425
4    White          224          42.911877

In [48]:
fig = px.pie(cook_county_deaths_cleaned_race, values='Racial Percentage', names='Race', color_discrete_sequence=px.colors.sequential.RdBu, title = "Cook County COVID19 Deaths by Race")


fig.update_traces(hoverinfo='label+percent', textinfo='percent+label', textfont_size=20,
                  marker=dict(line=dict(color='#000000', width=2)))
layout2 = go.Layout(
                    annotations = [dict(xref='paper',
                                        yref='paper',
                                        x=1.2, y=-0.25,
                                        showarrow=False,
                                        text ='El Khatib, data courtesy of Cook County Medical Examiner Case Archive')])

fig.update_layout(layout2)

fig.show()

In [49]:


fig = px.bar(cook_county_deaths_cleaned_age, title = "Cook County COVID19 Deaths by Age", x='AgeGroup', y='Age Percentage',
             hover_data=['Age Percentage'], color='AgeGroup', height=400, text = "Age Percentage", color_discrete_sequence=px.colors.sequential.RdBu)

fig.update_traces(texttemplate='%{text:.2s}%', textposition='outside')
fig.update_layout(uniformtext_minsize=8, uniformtext_mode='hide')
layout = go.Layout(
    font=dict(size=14),
    width=1050,
     height=550,
    xaxis_title = "Age Bracket",
    yaxis_title = "Percentage of COVID19 Deaths")
fig.update_layout(layout)
fig.update_layout(showlegend=False)

fig.show()

In [53]:
import geopandas as gpd
data = gpd.read_file('usa-hospital-beds_dataset.geojson')
bed_data = pd.DataFrame(data)
bed_data


ModuleNotFoundError: No module named 'geopandas'

In [ ]:
bed_data_drop_rows = bed_data[bed_data['FIPS'].isnull()].index
bed_data.drop(bed_data_drop_rows , inplace=True)

bed_data['FIPS'] = bed_data['FIPS'].astype(int)
county_race_covid_2019_df['COUNTY_FIPS'] = county_race_covid_2019_df['COUNTY_FIPS'].astype(int)


bed_data_demographic = pd.merge(bed_data, county_race_covid_2019_df, left_on = 'FIPS', right_on = 'COUNTY_FIPS', how = "inner")


In [ ]:
bed_data_demographic.head(500)

In [ ]:
import plotly.figure_factory as ff

colorscale = ["#f7fbff", "#ebf3fb", "#deebf7", "#d2e3f3", "#c6dbef", "#b3d2e9", "#9ecae1",
    "#85bcdb", "#6baed6", "#57a0ce", "#4292c6", "#3082be", "#2171b5", "#1361a9",
    "#08519c", "#0b4083", "#08306b"
]
endpts = list(np.linspace(1, 12, len(colorscale) - 1))
#fips = bed_data_demographic['FIPS'].tolist()
#values = bed_data_demographic['Unemployment Rate (%)'].tolist()


fig = ff.create_choropleth(
    fips=bed_data_demographic["FIPS"], values = bed_data_demographic["NUM_LICENSED_BEDS"], scope=['usa'],
    binning_endpoints=endpts, colorscale=colorscale,
    show_state_data=False,
    show_hover=True,
    asp = 2.9,
    title_text = 'USA',
    legend_title = 'NUM OF LICENSED BEDS'
)
fig.layout.template = None
fig.show()